In [1]:
import pandas as pd
import numpy as np
import altair as alt

In [2]:
# Run this cell to ensure that altair plots show up in the exported HTML
# and that the R cell magic works
import altair as alt

# Save a vega-lite spec and a PNG blob for each plot in the notebook
alt.renderers.enable('html')

# Handle large data sets without embedding them in the notebook
alt.data_transformers.enable('vegafusion')

DataTransformerRegistry.enable('vegafusion')

In [3]:
df_raw = pd.read_csv("data/SuperStoreOrders.csv")
df_raw.info()
df_raw.head()
df_raw.shape
df_raw.isna().sum()
df_raw.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51290 entries, 0 to 51289
Data columns (total 21 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   order_id        51290 non-null  object 
 1   order_date      51290 non-null  object 
 2   ship_date       51290 non-null  object 
 3   ship_mode       51290 non-null  object 
 4   customer_name   51290 non-null  object 
 5   segment         51290 non-null  object 
 6   state           51290 non-null  object 
 7   country         51290 non-null  object 
 8   market          51290 non-null  object 
 9   region          51290 non-null  object 
 10  product_id      51290 non-null  object 
 11  category        51290 non-null  object 
 12  sub_category    51290 non-null  object 
 13  product_name    51290 non-null  object 
 14  sales           51290 non-null  object 
 15  quantity        51290 non-null  int64  
 16  discount        51290 non-null  float64
 17  profit          51290 non-null 

quantity      discount        profit  shipping_cost          year
count  51290.000000  51290.000000  51290.000000   51290.000000  51290.000000
mean       3.476545      0.142908     28.641740      26.375915   2012.777208
std        2.278766      0.212280    174.424113      57.296804      1.098931
min        1.000000      0.000000  -6599.978000       0.000000   2011.000000
25%        2.000000      0.000000      0.000000       2.610000   2012.000000
50%        3.000000      0.000000      9.240000       7.790000   2013.000000
75%        5.000000      0.200000     36.810000      24.450000   2014.000000
max       14.000000      0.850000   8399.976000     933.570000   2014.000000

In [4]:
df = df_raw.copy()
df["sales"] = (
    df["sales"]
        .astype(str)                # ensure string
        .str.replace(",", "", regex=False)  # remove commas
        .str.strip()
)

df["sales"] = pd.to_numeric(df["sales"], errors="coerce")
df["order_date"] = pd.to_datetime(df["order_date"], format="mixed", dayfirst=True, errors="coerce")
df["ship_date"]  = pd.to_datetime(df["ship_date"],  format="mixed", dayfirst=True, errors="coerce")
df["shipping_delay"] = (df["ship_date"] - df["order_date"]).dt.days

In [5]:
df.info()
df.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51290 entries, 0 to 51289
Data columns (total 22 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   order_id        51290 non-null  object        
 1   order_date      51290 non-null  datetime64[ns]
 2   ship_date       51290 non-null  datetime64[ns]
 3   ship_mode       51290 non-null  object        
 4   customer_name   51290 non-null  object        
 5   segment         51290 non-null  object        
 6   state           51290 non-null  object        
 7   country         51290 non-null  object        
 8   market          51290 non-null  object        
 9   region          51290 non-null  object        
 10  product_id      51290 non-null  object        
 11  category        51290 non-null  object        
 12  sub_category    51290 non-null  object        
 13  product_name    51290 non-null  object        
 14  sales           51290 non-null  int64         
 15  qu

order_date                      ship_date  \
count                          51290                          51290   
mean   2013-05-11 21:26:49.155780864  2013-05-15 20:42:42.745174528   
min              2011-01-01 00:00:00            2011-01-03 00:00:00   
25%              2012-06-19 00:00:00            2012-06-23 00:00:00   
50%              2013-07-08 00:00:00            2013-07-12 00:00:00   
75%              2014-05-22 00:00:00            2014-05-26 00:00:00   
max              2014-12-31 00:00:00            2015-01-07 00:00:00   
std                              NaN                            NaN   

              sales      quantity      discount        profit  shipping_cost  \
count  51290.000000  51290.000000  51290.000000  51290.000000   51290.000000   
mean     246.498440      3.476545      0.142908     28.641740      26.375915   
min        0.000000      1.000000      0.000000  -6599.978000       0.000000   
25%       31.000000      2.000000      0.000000      0.000000       2.610000   
50%       85.000000      3.000000      0.000000      9.240000       7.790000   
75%      251.000000      5.000000      0.200000     36.810000      24.450000   
max    22638.000000     14.000000      0.850000   8399.976000     933.570000   
std      487.567175      2.278766      0.212280    174.424113      57.296804   

               year  shipping_delay  
count  51290.000000    51290.000000  
mean    2012.777208        3.969370  
min     2011.000000        0.000000  
25%     2012.000000        3.000000  
50%     2013.000000        4.000000  
75%     2014.000000        5.000000  
max     2014.000000        7.000000  
std        1.098931        1.729437

### Total Profit by Region
Where profit comes from geographically

In [6]:
g_region = (df.groupby("region", as_index=False)
              .agg(
                  orders=("order_id","nunique"),
                  sales=("sales","sum"),
                  profit=("profit","sum"),
                  avg_discount=("discount","mean")
              )
              .assign(margin=lambda x: x["profit"]/x["sales"])
              .sort_values("profit", ascending=False))

g_region

region  orders    sales        profit  avg_discount    margin
3          Central    5249  2822399  311403.98164      0.138851  0.110333
7            North    2356  1248192  194597.95252      0.096056  0.155904
8       North Asia    1150   848349  165578.42100      0.048717  0.195177
10           South    3270  1600960  140355.76618      0.149050  0.087670
4     Central Asia    1026   752839  132480.18700      0.067480  0.175974
9          Oceania    1744  1100207  121666.64200      0.153169  0.110585
12            West    1611   725514  108418.44890      0.109335  0.149437
6             East    1401   678834   91522.78000      0.145365  0.134824
0           Africa    2232   783776   88871.63100      0.156704  0.113389
5             EMEA    2462   806184   43897.97100      0.196083  0.054452
2        Caribbean     855   324281   34571.32104      0.135751  0.106609
11  Southeast Asia    1517   884438   17852.32900      0.272077  0.020185
1           Canada     201    66932   17817.39000      0.000000  0.266201

In [7]:
region_profit_scatter = alt.Chart(g_region).mark_circle(size=200).encode(
    x=alt.X("profit:Q", title="Total Profit"),
    y=alt.Y("sales:Q", title="Total Sales"),
    color=alt.Color(
        "avg_discount:Q",
        scale=alt.Scale(scheme="viridis"),
        title="Average Discount"
    ),
    tooltip=[
        "region:N",
        alt.Tooltip("profit:Q", format=",.2f"),
        alt.Tooltip("sales:Q", format=",.2f"),
        alt.Tooltip("margin:Q", format=".2%"),
        alt.Tooltip("avg_discount:Q", format=".2f")
    ]
).properties(
    width=600,
    height=400,
    title="Profit vs Sales by Region (Colored by Avg Discount)"
)

region_profit_scatter

alt.Chart(...)

### Profit by Category & Sub-category
Which products drive or destroy profit


In [8]:
g_product = (df.groupby(["category","sub_category"], as_index=False)
               .agg(
                   sales=("sales","sum"),
                   profit=("profit","sum"),
                   quantity=("quantity","sum"),
                   avg_discount=("discount","mean")
               )
               .assign(margin=lambda x: x["profit"]/x["sales"])
               .sort_values("profit"))

g_product

category sub_category    sales        profit  quantity  \
3         Furniture       Tables   757034  -64083.38870      3083   
8   Office Supplies    Fasteners    83254   11525.42410      8390   
9   Office Supplies       Labels    73433   15010.51200      9322   
12  Office Supplies     Supplies   243090   22583.26310      8543   
7   Office Supplies    Envelopes   170926   29601.11630      8380   
2         Furniture  Furnishings   385609   46967.42550     11225   
5   Office Supplies          Art   372163   57953.91090     16301   
15       Technology     Machines   779071   58867.87300      4906   
10  Office Supplies        Paper   244307   59207.68270     12822   
6   Office Supplies      Binders   461952   72449.84600     21429   
11  Office Supplies      Storage  1127124  108461.48980     16917   
13       Technology  Accessories   749307  129626.30620     10946   
4   Office Supplies   Appliances  1011081  141680.58940      6078   
1         Furniture       Chairs  1501682  141973.79750     12336   
0         Furniture    Bookcases  1466559  161924.41950      8310   
16       Technology       Phones  1706874  216717.00580     11870   
14       Technology      Copiers  1509439  258567.54818      7454   

    avg_discount    margin  
3       0.290732 -0.084651  
8       0.140595  0.138437  
9       0.120449  0.204411  
12      0.127918  0.092901  
7       0.131749  0.173181  
2       0.151066  0.121801  
5       0.117362  0.155722  
15      0.169583  0.075562  
10      0.109469  0.242350  
6       0.179207  0.156834  
11      0.138464  0.096229  
13      0.120481  0.172995  
4       0.141709  0.140128  
1       0.163110  0.094543  
0       0.153758  0.110411  
16      0.145847  0.126967  
14      0.117147  0.171300

In [9]:
category_profit_bar = alt.Chart(g_product).mark_bar().encode(
    y=alt.Y(
        "category:N",
        sort="-x",
        title="Category"
    ),
    x=alt.X(
        "profit:Q",
        title="Total Profit"
    ),
    color=alt.condition(
        alt.datum.profit > 0,
        alt.value("steelblue"),
        alt.value("firebrick")
    ),
    tooltip=[
        "category:N",
        alt.Tooltip("profit:Q", format=",.2f"),
        alt.Tooltip("sales:Q", format=",.2f")
    ]
).properties(
    width=600,
    height=300,
    title="Total Profit by Category"
)

category_profit_bar

alt.Chart(...)

In [10]:
product_profit_bar = alt.Chart(g_product).mark_bar().encode(
    y=alt.Y(
        "sub_category:N",
        sort="-x",
        title="Sub-Category"
    ),
    x=alt.X(
        "profit:Q",
        title="Total Profit"
    ),
    color=alt.condition(
        alt.datum.profit > 0,
        alt.value("steelblue"),
        alt.value("firebrick")
    ),
    tooltip=[
        "category:N",
        "sub_category:N",
        alt.Tooltip("profit:Q", format=",.2f"),
        alt.Tooltip("sales:Q", format=",.2f"),
        alt.Tooltip("margin:Q", format=".2%"),
        alt.Tooltip("avg_discount:Q", format=".2f")
    ]
).properties(
    width=650,
    height=450,
    title="Profit by Product Sub-Category"
)

product_profit_bar

alt.Chart(...)

### Profit trends over time

In [11]:
g_year = (df.groupby("year", as_index=False)
            .agg(
                sales=("sales","sum"),
                profit=("profit","sum")
            )
            .assign(margin=lambda x: x["profit"]/x["sales"]))

g_year

year    sales        profit    margin
0  2011  2259511  248940.81154  0.110175
1  2012  2677493  307415.27910  0.114815
2  2013  3405860  408512.76018  0.119944
3  2014  4300041  504165.97046  0.117247

In [12]:
profit_trend = alt.Chart(g_year).mark_line(point=True).encode(
    x=alt.X("year:O", title="Year"),
    y=alt.Y("profit:Q", title="Total Profit"),
    tooltip=[
        "year:O",
        alt.Tooltip("profit:Q", format=",.2f"),
        alt.Tooltip("sales:Q", format=",.2f"),
        alt.Tooltip("margin:Q", format=".2%")
    ]
).properties(
    width=600,
    height=350,
    title="Profit Trend Over Time"
)

profit_trend

alt.Chart(...)

In [13]:
import altair as alt

profit_region = (
    df.groupby("region", as_index=False)
      .agg(total_profit=("profit", "sum"))
)

profit_chart = alt.Chart(profit_region).mark_bar().encode(
    y=alt.Y(
        "region:N",
        sort="-x",
        title="Region"
    ),
    x=alt.X(
        "total_profit:Q",
        title="Total Profit"
    ),
    color=alt.condition(
        alt.datum.total_profit > 0,
        alt.value("steelblue"),
        alt.value("firebrick")
    ),
    tooltip=[
        alt.Tooltip("region:N", title="Region"),
        alt.Tooltip("total_profit:Q", format=",.2f", title="Total Profit")
    ]
).properties(
    width=600,
    height=350,
    title="Total Profit by Region"
)

profit_chart

alt.Chart(...)

In [14]:
df.groupby(["market", "region"])["country"].nunique().sort_values(ascending=False)


market  region        
Africa  Africa            45
EMEA    EMEA              40
LATAM   South             10
        Caribbean          8
APAC    Southeast Asia     8
        Central Asia       6
EU      Central            6
        North              6
APAC    North Asia         6
LATAM   Central            5
EU      South              3
APAC    Oceania            3
Canada  Canada             1
LATAM   North              1
US      Central            1
        East               1
        South              1
        West               1
Name: country, dtype: int64

In [15]:
# Make sure these have region/category as columns, not index
g_region = g_region.reset_index() if "region" not in g_region.columns else g_region
g_product = g_product.reset_index() if "sub_category" not in g_product.columns else g_product

region_select = alt.selection_point(fields=["region"], empty="all")

region_bar = alt.Chart(g_region).mark_bar().encode(
    y=alt.Y("region:N", sort="-x"),
    x=alt.X("profit:Q", title="Total Profit"),
    tooltip=["region:N", alt.Tooltip("profit:Q", format=",.0f")],
    opacity=alt.condition(region_select, alt.value(1), alt.value(0.3))
).add_params(region_select).properties(
    width=300, height=300, title="Click a Region"
)

subcat_bar = alt.Chart(df).transform_filter(
    region_select
).mark_bar().encode(
    y=alt.Y("sub_category:N", sort="-x"),
    x=alt.X("sum(profit):Q", title="Profit"),
    tooltip=["sub_category:N", alt.Tooltip("sum(profit):Q", format=",.0f")]
).properties(
    width=400, height=300, title="Sub-Category Profit (Filtered)"
)

(region_bar | subcat_bar)

alt.HConcatChart(...)

In [16]:
market_options = sorted(df["market"].unique().tolist())

market_param = alt.param(
    name="Market",
    bind=alt.binding_select(options=market_options),
    value=market_options[0]
)

profit_by_region = alt.Chart(df).add_params(market_param).transform_filter(
    alt.datum.market == market_param
).mark_bar().encode(
    y=alt.Y("region:N", sort="-x"),
    x=alt.X("sum(profit):Q", title="Total Profit"),
    tooltip=["region:N", alt.Tooltip("sum(profit):Q", format=",.0f")]
).properties(
    width=600, height=300, title="Profit by Region (Filtered by Market Dropdown)"
)

profit_by_region

alt.Chart(...)

In [17]:
df_raw.describe()

quantity      discount        profit  shipping_cost          year
count  51290.000000  51290.000000  51290.000000   51290.000000  51290.000000
mean       3.476545      0.142908     28.641740      26.375915   2012.777208
std        2.278766      0.212280    174.424113      57.296804      1.098931
min        1.000000      0.000000  -6599.978000       0.000000   2011.000000
25%        2.000000      0.000000      0.000000       2.610000   2012.000000
50%        3.000000      0.000000      9.240000       7.790000   2013.000000
75%        5.000000      0.200000     36.810000      24.450000   2014.000000
max       14.000000      0.850000   8399.976000     933.570000   2014.000000

# EDA

## Describe your data

This data set contains over 51000 retail orders from a global supertore between 2011 and 2014 [found here](https://www.kaggle.com/datasets/aashwinkumar/superstore-sales-dataset). Each row contains a prodcuct-level order and includes infromatino about sales, profit, discount, shipping cost, customer segment, product category, and geographic market.


## Load the dataset

The following loaded the dataset
```python
df_raw = pd.read_csv("data/SuperStoreSales.csv")
```


## Explore the dataset

The data was explored with: 
```python 
df_raw.info()
df_raw.head()
df_raw.shape
df_raw.isna().sum()
df_raw.describe()
```
- With these lines of code, we see that this dataset does not contain missing values. We see columns we need to data wrangle like `sales` is in an object dtype form instead of numeric.
- We also see the 5 number summary for different columns in the dataset. The nost notable is `profit` where we see the min is $-6599.98 and the max is $8399.98.
- We also see the shape of the dataset, which is: (51290, 21).


## Inital thoughts

Profit appears to be to be highly variable with some extreme negative values. Discounts range from 0\% to 85\% suggesting pricing strategy may influence profitability. 


## Wrangling

This dataset did not contain missing values, so distribution-preserving wrangling techniques were not required.

```python 
df["sales"] = (
    df["sales"]
        .astype(str)                # ensure string
        .str.replace(",", "", regex=False)  # remove commas
        .str.strip()
)

df["sales"] = pd.to_numeric(df["sales"], errors="coerce")
df["order_date"] = pd.to_datetime(df["order_date"], format="mixed", dayfirst=True, errors="coerce")
df["ship_date"]  = pd.to_datetime(df["ship_date"],  format="mixed", dayfirst=True, errors="coerce")
df["shipping_delay"] = (df["ship_date"] - df["order_date"]).dt.days
```

- `sales` was converted from object to numeric. Some sales values contained commas (e.g., “1,234”), which needed to be removed before conversion to ensure accurate numeric parsing 
- The `order_date` and `ship_date`columns were converted to pandas datetime format to enable time-based analysis
- A new column, `shipping_delay`, was created by being the difference (in dates) between `ship_date` and `order_date`.


## Research Questions

- Which markets and regions generate the highest and lowest profit
- Which product sub-categories drive or destroy profit
- How do discounts impact profit margins
- How has profitability changed over time

## Data Analysis and Visualizations

This is done with the different group by statments, and the visuals that followed.

There is inter-plot with: 
```python
# Make sure these have region/category as columns, not index
g_region = g_region.reset_index() if "region" not in g_region.columns else g_region
g_product = g_product.reset_index() if "sub_category" not in g_product.columns else g_product

region_select = alt.selection_point(fields=["region"], empty="all")

region_bar = alt.Chart(g_region).mark_bar().encode(
    y=alt.Y("region:N", sort="-x"),
    x=alt.X("profit:Q", title="Total Profit"),
    tooltip=["region:N", alt.Tooltip("profit:Q", format=",.0f")],
    opacity=alt.condition(region_select, alt.value(1), alt.value(0.3))
).add_params(region_select).properties(
    width=300, height=300, title="Click a Region"
)

subcat_bar = alt.Chart(df).transform_filter(
    region_select
).mark_bar().encode(
    y=alt.Y("sub_category:N", sort="-x"),
    x=alt.X("sum(profit):Q", title="Profit"),
    tooltip=["sub_category:N", alt.Tooltip("sum(profit):Q", format=",.0f")]
).properties(
    width=400, height=300, title="Sub-Category Profit (Filtered)"
)

(region_bar | subcat_bar)
```

The plots have intra-plot by using `tooltips` in the plotting.

There is a plot with a widget since we can select the region.

```python 
market_options = sorted(df["market"].unique().tolist())

market_param = alt.param(
    name="Market",
    bind=alt.binding_select(options=market_options),
    value=market_options[0]
)

profit_by_region = alt.Chart(df).add_params(market_param).transform_filter(
    alt.datum.market == market_param
).mark_bar().encode(
    y=alt.Y("region:N", sort="-x"),
    x=alt.X("sum(profit):Q", title="Total Profit"),
    tooltip=["region:N", alt.Tooltip("sum(profit):Q", format=",.0f")]
).properties(
    width=600, height=300, title="Profit by Region (Filtered by Market Dropdown)"
)

profit_by_region
```

## Summary and Conclusions

- We see that technology products drive the majority of profits. 
- Furniture generates many losses for 
- Regions with higher discount levels tend to generate lower profit relative to sales. In particular, regions with discounts above 20\$ have weak profitability despite moderate sales. 

